In [0]:
%run ../_utils

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
from pyspark.sql.functions import col, count


# Customers orders

Essa é uma tabela de sumarização.

O objetivo dela é responder sobre as compras dos clientes.

Conseguiríamos responder questões como:
 - Quantas vendas ocorreram por estado
 - poderiamos ver as vendas por mes e ano
 - poderiamos ver dados sobre valores das vendas
 - dados sobre as entregas, como a relação do dia da compra e atraso na entrega

In [0]:
tb_name = "olist_gold.customer_orders"
dataset_location = "olist_customer_ordersdataset"
target_location = f"dbfs:/FileStore/delta/brazilian_ecommerce/{dataset_location}/gold"

## 1 - Data ingestion


In [0]:
df_orders = spark.read.table("olist_gold.orders") # leituira da delta table central, orders (ja da propria gold)
df_customers = spark.sql("select * from olist_silver.customers") # leitura da delta table, outra maneira


## 2 - preparation

In [0]:
df = df_orders.join(df_customers, on="customer_id", how="left")

In [0]:
display(df)

customer_id order_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date month_year minutes_to_approve days_to_deliver hours_to_deliver total_elapsed_days total_elapsed_hours overdue delay_hours delay_days day_of_week weekend total_payment_sequential total_payment_value payment_types review_id review_score review_comment_title review_comment_message review_creation_date review_answer_timestamp customer_unique_id customer_zip_code_prefix customer_city customer_state 9ef432eb6251297304e76186b10a928d e481f51cbdc54678b7cc49136f2d6af7 delivered 2017-10-02T10:56:33Z 2017-10-02T11:07:15Z 2017-10-04T19:55:00Z 2017-10-10T21:25:13Z 2017-10-18T00:00:00Z 10-2017 10.7 6.06 145.5 8.44 202.48 true 170.58 7.11 Segunda-feira false 3 38.71 List(credit_card, voucher) a54f0611adc9ed256b57ede6b6eb5114 4 null Não testei o produto ainda, mas ele veio correto e em boas condições. Apenas a caixa que veio bem amassada e danificada, o que ficará chato, pois se trata de um presente. 2017-10-11T00:00:00Z 2017-10-12T03:43:48Z 7c396fd4830fd04220f754e42b4e5bff 3149 sao paulo SP b0830fb4747a6c6d20dea0b8c802d7ef 53cdb2fc8bc7dce0b6741e2150273451 delivered 2018-07-24T20:41:37Z 2018-07-26T03:24:27Z 2018-07-26T14:31:00Z 2018-08-07T15:27:45Z 2018-08-13T00:00:00Z 07-2018 1842.83 12.04 288.95 13.78 330.77 true 128.54 5.36 Terça-feira false 1 141.46 List(boleto) 8d5266042046a06655c8db133d120ba5 4 Muito boa a loja Muito bom o produto. 2018-08-08T00:00:00Z 2018-08-08T18:37:50Z af07308b275d755c9edb36a90c618231 47813 barreiras BA 41ce2a54c0b03bf3443c3d931a367089 47770eb9100c2d0c44946d9cf07ec65d delivered 2018-08-08T08:38:49Z 2018-08-08T08:55:23Z 2018-08-08T13:50:00Z 2018-08-17T18:06:29Z 2018-09-04T00:00:00Z 08-2018 16.57 9.18 220.27 9.39 225.46 true 413.89 17.25 Quarta-feira false 1 179.12 List(credit_card) e73b67b67587f7644d5bd1a52deb1b01 5 null null 2018-08-18T00:00:00Z 2018-08-22T19:07:58Z 3a653a41f6f9fc3d2a113cf8398680e8 75265 vianopolis GO f88197465ea7920adcdbec7375364d82 949d5b44dbf5de918fe9c16f97b45f8a delivered 2017-11-18T19:28:06Z 2017-11-18T19:45:59Z 2017-11-22T13:39:59Z 2017-12-02T00:28:42Z 2017-12-15T00:00:00Z 11-2017 17.88 9.45 226.81 13.21 317.01 true 311.52 12.98 Sábado true 1 72.2 List(credit_card) 359d03e676b3c069f62cadba8dd3f6e8 5 null O produto foi exatamente o que eu esperava e estava descrito no site e chegou bem antes da data prevista. 2017-12-03T00:00:00Z 2017-12-05T19:21:58Z 7c142cf63193a1473d2e66489a9ae977 59296 sao goncalo do amarante RN 8ab97904e6daea8866dbdbc4fb7aad2c ad21c59c0840e6cb83a9ceb5573f8159 delivered 2018-02-13T21:18:39Z 2018-02-13T22:20:29Z 2018-02-14T19:46:34Z 2018-02-16T18:17:02Z 2018-02-26T00:00:00Z 02-2018 61.83 1.94 46.51 2.87 68.97 true 221.72 9.24 Terça-feira false 1 28.62 List(credit_card) e50934924e227544ba8246aeb3770dd4 5 null null 2018-02-17T00:00:00Z 2018-02-18T13:02:51Z 72632f0f9dd73dfee390c9b22eb56dd6 9195 santo andre SP 503740e9ca751ccdda7ba28e9ab8f608 a4591c265e18cb1dcee52889e2d8acc3 delivered 2017-07-09T21:57:05Z 2017-07-09T22:10:13Z 2017-07-11T14:58:04Z 2017-07-26T10:57:55Z 2017-08-01T00:00:00Z 07-2017 13.13 14.83 356.0 16.54 397.01 true 133.03 5.54 Domingo true 1 175.26 List(credit_card) 89b738e70a1ce346db29a20fb2910161 4 null null 2017-07-27T00:00:00Z 2017-07-27T22:48:30Z 80bb27c7c16e8f973207a5086ab329e2 86320 congonhinhas PR ed0271e0b7da060a393796590e7b737a 136cce7faa42fdb2cefd53fdc79a6098 invoiced 2017-04-11T12:22:08Z 2017-04-13T13:25:17Z null null 2017-05-09T00:00:00Z 04-2017 2943.15 null null null null false 0.0 0.0 Terça-feira false 1 65.95 List(credit_card) e07549ef5311abcc92ba1784b093fb56 2 null fiquei triste por n ter me atendido. 2017-05-13T00:00:00Z 2017-05-13T20:25:42Z 36edbb3fb164b1f16485364b6fb04c73 98900 santa rosa RS 9bdf08b4b3b52b5526ff42d37d47f222 6514b8ad8028c9f2cc2374ded245783f delivered 2017-05-16T13:10:30Z 2017-05-16T13:22:11Z 2017-05-22T10:07:46Z 2017-05-26T12:55:51Z 2017-06-07T00:00:00Z 05-2017 11.68


## Saving data

In [0]:
save_dataframe(df, format_mode="delta", table_name=tb_name, target_location=target_location)

[LOG] Saving olist_gold.customer_orders delta on dbfs:/FileStore/delta/brazilian_ecommerce/olist_customer_ordersdataset/gold... OK!



## create delta table


In [0]:
create_table(table_name=tb_name, target_location=target_location)

[LOG] Creating delta table olist_gold.customer_orders on dbfs:/FileStore/delta/brazilian_ecommerce/olist_customer_ordersdataset/gold... OK!


In [0]:
# exit para fechar a execução
dbutils.notebook.exit("OK")

In [0]:
%sql

select * from olist_gold.orders